In [1]:
import sys
import pandas as pd
import numpy as np
import sklearn

# 导入一些算法
from sklearn import ensemble
# 用于编码转换
from sklearn.preprocessing import LabelEncoder
# 用于特征选择
from sklearn import feature_selection

from sklearn import model_selection
# 用于评估模型
from sklearn import metrics

import matplotlib as mpl
import matplotlib.pyplot as plt
import seaborn as sns
%matplotlib inline

# 设置绘图风格
mpl.style.use('ggplot')

In [2]:
base_path = 'dataset_temp/titanic'
data_all = pd.read_csv(f'{base_path}/data_all.csv')
# 拆分data_all为训练集和测试集
data_train = data_all[data_all['type'] == 'train'].copy()
data_test = data_all[data_all['type'] == 'test'].copy()
print(data_train.shape)
print(data_test.shape)
data_train.head()

# 选择一些特征来进行训练



(891, 22)
(418, 22)


passengerid  survived  pclass  \
0            1         0       3   
1            2         1       1   
2            3         1       3   
3            4         1       1   
4            5         0       3   

                                                name     sex   age  sibsp  \
0                            Braund, Mr. Owen Harris    male  22.0      1   
1  Cumings, Mrs. John Bradley (Florence Briggs Th...  female  38.0      1   
2                             Heikkinen, Miss. Laina  female  26.0      0   
3       Futrelle, Mrs. Jacques Heath (Lily May Peel)  female  35.0      1   
4                           Allen, Mr. William Henry    male  35.0      0   

   parch            ticket     fare  ... family_size is_alone  title  \
0      0         A/5 21171   7.2500  ...           2        0     Mr   
1      0          PC 17599  71.2833  ...           2        0    Mrs   
2      0  STON/O2. 3101282   7.9250  ...           1        1   Miss   
3      0            113803  53.1000  ...           2        0    Mrs   
4      0            373450   8.0500  ...           1        1     Mr   

         fare_bin       age_bin sex_code embarked_code  title_code  fare_code  \
0  (-0.512, 51.2]  (16.0, 24.0]        1             2          12          0   
1   (51.2, 102.4]  (32.0, 40.0]        0             0          13          1   
2  (-0.512, 51.2]  (24.0, 32.0]        0             2           9          0   
3   (51.2, 102.4]  (32.0, 40.0]        0             2          13          1   
4  (-0.512, 51.2]  (32.0, 40.0]        1             2          12          0   

   age_code  
0         2  
1         4  
2         3  
3         4  
4         4  

[5 rows x 22 columns]

In [3]:
target  = ['survived']
features = ['pclass','sex',"sex_code","age_code","fare_code","embarked_code","embarked","is_alone","family_size","title_code","title"]

all_columns = target + features
data_train_dummies = pd.get_dummies(data_train[all_columns])
dummies_features = data_train_dummies.columns.to_list()
dummies_features.remove('survived')
print(dummies_features)

# # 训练集
x_train = data_train_dummies[dummies_features]
y_train = data_train_dummies[target]

# # 测试集
x_test = data_train_dummies[dummies_features]
y_test = data_train_dummies[target]


['pclass', 'sex_code', 'age_code', 'fare_code', 'embarked_code', 'is_alone', 'family_size', 'title_code', 'sex_female', 'sex_male', 'embarked_C', 'embarked_Q', 'embarked_S', 'title_Capt', 'title_Col', 'title_Don', 'title_Dr', 'title_Jonkheer', 'title_Lady', 'title_Major', 'title_Master', 'title_Miss', 'title_Mlle', 'title_Mme', 'title_Mr', 'title_Mrs', 'title_Ms', 'title_Rev', 'title_Sir', 'title_the Countess']


### 随机森林实现

In [4]:
# 为了自动处理超参数
from sklearn.model_selection import GridSearchCV

from sklearn.ensemble import RandomForestClassifier

rf = RandomForestClassifier(max_features='sqrt', random_state=1, n_jobs=-1)

# 这里有更合适的参数么？
#  oob_score 用于
param_grid = {
                "criterion": ['gini','entropy'],
                "min_samples_leaf": [1, 5, 10, 25],
                'min_samples_split': [2, 4, 10, 12, 16, 18, 25, 35],
                "n_estimators": [25, 50,100, 150], 
                'max_depth': [3, 5, 15, 25, 30],
                'max_features': ['sqrt'],
                'oob_score': [True]
            }

gs = GridSearchCV(estimator=rf, param_grid=param_grid, scoring='accuracy', cv=3, n_jobs=-1)
gs = gs.fit(x_train, y_train)

/opt/anaconda3/envs/ai_trader/lib/python3.11/site-packages/sklearn/base.py:1473: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  return fit_method(estimator, *args, **kwargs)
/opt/anaconda3/envs/ai_trader/lib/python3.11/site-packages/sklearn/base.py:1473: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  return fit_method(estimator, *args, **kwargs)
/opt/anaconda3/envs/ai_trader/lib/python3.11/site-packages/sklearn/base.py:1473: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  return fit_method(estimator, *args, **kwargs)
/opt/anaconda3/envs/ai_trader/lib/python3.11/site-packages/sklearn/base.py:1473: DataConversionWarning: A column-vector y was passed when a 1d array

In [5]:
# 最佳参数
print(gs.best_params_)
print(gs.best_score_)

{'criterion': 'entropy', 'max_depth': 15, 'max_features': 'sqrt', 'min_samples_leaf': 1, 'min_samples_split': 25, 'n_estimators': 100, 'oob_score': True}
0.8361391694725028


In [9]:

# 创建一个新的随机森林对象，放入最佳参数, 重新fit
best_params = gs.best_params_
rf2 = RandomForestClassifier(criterion=best_params['criterion'], 
                             n_estimators=best_params['n_estimators'],
                             min_samples_split=best_params['min_samples_split'],
                             min_samples_leaf=best_params['min_samples_leaf'],
                             max_features=best_params['max_features'],
                             max_depth=best_params['max_depth'],
                             oob_score=best_params['oob_score'],
                             random_state=1,
                             n_jobs=-1)
rf2.fit(x_train, y_train)

/opt/anaconda3/envs/ai_trader/lib/python3.11/site-packages/sklearn/base.py:1473: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  return fit_method(estimator, *args, **kwargs)


RandomForestClassifier(criterion='entropy', max_depth=15, min_samples_split=25,
                       n_jobs=-1, oob_score=True, random_state=1)

In [10]:
df1 = pd.DataFrame(x_train.columns,columns=['Variable'])
df2 = pd.DataFrame(rf2.feature_importances_,columns=['Importance'])
pd.concat([df1,df2],axis=1).sort_values(by='Importance',ascending=False)


Variable  Importance
1             sex_code    0.144756
0               pclass    0.142216
24            title_Mr    0.116431
9             sex_male    0.083285
8           sex_female    0.082805
2             age_code    0.081528
6          family_size    0.070403
3            fare_code    0.063930
7           title_code    0.063654
25           title_Mrs    0.032750
21          title_Miss    0.027144
20        title_Master    0.016829
5             is_alone    0.016656
4        embarked_code    0.016035
12          embarked_S    0.011497
10          embarked_C    0.011145
11          embarked_Q    0.008070
27           title_Rev    0.003890
16            title_Dr    0.001883
14           title_Col    0.001482
28           title_Sir    0.001010
19         title_Major    0.000829
22          title_Mlle    0.000323
15           title_Don    0.000321
26            title_Ms    0.000307
13          title_Capt    0.000300
17      title_Jonkheer    0.000236
29  title_the Countess    0.000106
23           title_Mme    0.000090
18          title_Lady    0.000089

In [12]:
# 正式预测
pred = rf2.predict(x_test)
# 与真实值比较
print(metrics.accuracy_score(y_test,pred))


0.8552188552188552
